In [1]:
import torch
import matplotlib.pyplot as plt
import numpy as np
import cv2
import pickle
from adaptive import Encoder2Decoder
from utils import CocoImageFolder, coco_eval, to_var, show_images
from torch.autograd import Variable 
from torchvision import transforms
from build_vocab import Vocabulary

In [2]:
pretrained = 'models-attentive/adaptive-1.pkl'
images_path = './data/resized/'
vocab_path = './data/vocab.pkl'
caption_val_path = './data/annotations/captions_val2017.json'
eval_size = 10 
num_workers = 4

In [3]:
with open( vocab_path, 'rb') as f:
    vocab = pickle.load( f )

In [4]:
# Image transformation
transform = transforms.Compose([ 
    transforms.ToTensor(), 
    transforms.Normalize((0.485, 0.456, 0.406), 
                         (0.229, 0.224, 0.225))])

In [5]:
# Define model and load pretrained
model = Encoder2Decoder( 256, len( vocab ), 512 )
model.load_state_dict( torch.load( pretrained ) )
model.eval()

Encoder2Decoder(
  (encoder): AttentiveCNN(
    (vgg_conv): Sequential(
      (0): Sequential(
        (0): Conv2d(3, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (1): ReLU(inplace)
        (2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (3): ReLU(inplace)
        (4): MaxPool2d(kernel_size=(2, 2), stride=(2, 2), dilation=(1, 1), ceil_mode=False)
        (5): Conv2d(64, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (6): ReLU(inplace)
        (7): Conv2d(128, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (8): ReLU(inplace)
        (9): MaxPool2d(kernel_size=(2, 2), stride=(2, 2), dilation=(1, 1), ceil_mode=False)
        (10): Conv2d(128, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (11): ReLU(inplace)
        (12): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (13): ReLU(inplace)
        (14): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(

In [10]:
if torch.cuda.is_available():
    model.cuda()

In [7]:
model = Encoder2Decoder( 256, len( vocab ), 512 )

In [8]:
# Evaluation image loader
cocoFolder = CocoImageFolder( images_path, caption_val_path, transform )
eval_data_loader = torch.utils.data.DataLoader( 
        cocoFolder, 
        batch_size = eval_size, 
        shuffle = False, num_workers = num_workers)

In [18]:
from data_loader import get_loader 
# Build training data loader
data_loader = get_loader( './data/', './data/annotations/captions_val2017.json', vocab, 
                          transform, 30,
                          shuffle=True, num_workers=4) 

loading annotations into memory...
Done (t=0.05s)
creating index...
index created!


In [13]:
for idx, (images, image_ids, filenames ) in enumerate( eval_data_loader ):
    images = to_var( images )
    generated_captions, attention, beta = model.sampler( images )
    
    captions = generated_captions.cpu().data.numpy()
    attention = attention.view( attention.size(0), attention.size(1), 7, 7 ).cpu().data.numpy()
    
    beta = beta.view( beta.size(0), beta.size(1) ).cpu().data.numpy()
    
    for image_idx in range( captions.shape[ 0 ] ):
        
        sampled_ids = captions[ image_idx ]
        sampled_caption = []
        
        for word_id in sampled_ids:
                
            word = vocab.idx2word[ word_id ]
            if word == '<end>':
                break
            else:
                sampled_caption.append( word )
        
        cap_len = len( sampled_caption )
        sentence = ' '.join( sampled_caption )
        image_attention = attention[ image_idx, :cap_len, :, : ]
        language_sentinel = beta[ image_idx, :cap_len ]
        
        # Create the Graph
        image_seq = []
        titles = []
        img = cv2.imread( images_path + filenames[ image_idx ] )
        img = cv2.cvtColor( img, cv2.COLOR_BGR2RGB )
        
        for cap_idx, word in enumerate( sampled_caption ):
            
            height, width, _ = img.shape
            
            heatmap = image_attention[ cap_idx ] * 7 # 7x7 attention map
            heatmap = np.uint8( heatmap * 255 )
            heatmap = cv2.applyColorMap( cv2.resize( heatmap, ( width, height ) ), cv2.COLORMAP_JET )
            
            result = np.uint8( heatmap * 0.4  + img * 0.5  )
            image_seq.append( result )
            
            info = word + ' [%.2f]'%( language_sentinel[ cap_idx ] )
            titles.append( info )
        
        # Plot the attention images each row with 4 columns
        print('Attention Map of image:', filenames[ image_idx ])
        print('Generated caption:', sentence)
        show_images( image_seq, 4, titles )
        print('')

/home/kydn8237872/AdaptiveAttention/adaptive.py:91: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  alpha_t = F.softmax( z_t.view( -1, z_t.size( 2 ) ) ).view( z_t.size( 0 ), z_t.size( 1 ), -1 )
/home/kydn8237872/AdaptiveAttention/adaptive.py:103: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  alpha_hat_t = F.softmax( extended.view( -1, extended.size( 2 ) ) ).view( extended.size( 0 ), extended.size( 1 ), -1 )


Attention Map of image: 000000435206.jpg
Generated caption: bought kimono lightly mode happy trip viewing fox goes versions peopel control thatched crumbled cocktail cocktail cocktail versions cast cocktail



Attention Map of image: 000000016010.jpg
Generated caption: manipulating ' models facing models tangerines unaware couches thatched sleeve yellow nightstand heritage dash florets streaks markers stole decaying teaches


Process Process-9:
Process Process-12:
Process Process-11:
Process Process-10:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/kydn8237872/.pyenv/versions/3.5.2/lib/python3.5/multiprocessing/process.py", line 249, in _bootstrap
    self.run()
  File "/home/kydn8237872/.pyenv/versions/3.5.2/lib/python3.5/multiprocessing/process.py", line 249, in _bootstrap
    self.run()
  File "/home/kydn8237872/.pyenv/versions/3.5.2/lib/python3.5/multiprocessing/process.py", line 249, in _bootstrap
    self.run()
  File "/home/kydn8237872/.pyenv/versions/3.5.2/lib/python3.5/multiprocessing/process.py", line 249, in _bootstrap
    self.run()
  File "/home/kydn8237872/.pyenv/versions/3.5.2/lib/python3.5/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/kydn8237872/.pyenv/versions/3.5.2/lib/python3.5/multiprocessing/process.py", line 93, in run
 

KeyboardInterrupt: 